#  Consignes

## Description

Ouvrir le fichier ks-projects-201801.csv, il recense environ 100 000 projets KickStarter. Intégrer les données directement avec L'API Python dans une base de données Mongo. 

Il conviendra de bien spécifier manuellement l'ID du document. Pensez aussi à bien formatter le type des données pour profiter des méthodes implémentées par Mongo. L'ensemble de données n'est pas forcément nécessaire, c'est à vous de créer votre modèle de données.

## Questions

- 1) Récupérer les 5 projets ayant reçu le plus de promesse de dons.
- 2) Compter le nombre de projets ayant atteint leur but.
- 3) Compter le nombre de projets pour chaque catégorie.
- 4) Compter le nombre de projets français ayant été instanciés avant 2016.
- 5) Récupérer les projets américains ayant demandé plus de 200 000 dollars.
- 6) Compter le nombre de projet ayant "Sport" dans leur nom

In [22]:
import pandas as pd
import pymongo

In [23]:
client = pymongo.MongoClient()
database = client['exercices']
collection = database['kickstarter']

In [24]:
df_ks = pd.read_csv("./data/ks-projects-201801-sample.csv")

C:\Users\alexa\AppData\Local\Temp\ipykernel_12400\963325589.py:1: DtypeWarning: Columns (6,8,10,12) have mixed types. Specify dtype option on import or set low_memory=False.
  df_ks = pd.read_csv("./data/ks-projects-201801-sample.csv")


Ce warning intervient lorsque pandas n'arrive pas à inférer le type de données. Il est sympa il précise les colones 6,8,10,12. 

In [25]:
df_ks.columns[[6,8,10,12]]

Index(['goal', 'pledged', 'backers', 'usd pledged'], dtype='object')

## Question 0

### Netoyer les données

In [26]:
# Conversion des colonnes en types numériques
df_ks['ID'] = pd.to_numeric(df_ks['ID'], errors='coerce')
df_ks['goal'] = pd.to_numeric(df_ks['goal'], errors='coerce')
df_ks['pledged'] = pd.to_numeric(df_ks['pledged'], errors='coerce')
df_ks['usd pledged'] = pd.to_numeric(df_ks['usd pledged'], errors='coerce')
df_ks['usd_pledged_real'] = pd.to_numeric(df_ks['usd_pledged_real'], errors='coerce')
df_ks['backers'] = pd.to_numeric(df_ks['backers'], errors='coerce')

# Conversion des colonnes de dates
df_ks['deadline'] = pd.to_datetime(df_ks['deadline'], errors='coerce')
df_ks['launched'] = pd.to_datetime(df_ks['launched'], errors='coerce')

# Conversion des colonnes de texte en chaînes de caractères
df_ks['name'] = df_ks['name'].astype(str, errors='ignore')
df_ks['category'] = df_ks['category'].astype(str, errors='ignore')
df_ks['main_category'] = df_ks['main_category'].astype(str, errors='ignore')
df_ks['currency'] = df_ks['currency'].astype(str, errors='ignore')
df_ks['state'] = df_ks['state'].astype(str, errors='ignore')
df_ks['country'] = df_ks['country'].astype(str, errors='ignore')

# Suppression des lignes et des colonnes avec NaN et des doublons
df_ks = df_ks.dropna() 
df_ks = df_ks.dropna(axis=1) 
df_ks = df_ks.drop_duplicates()


In [27]:
df_ks.info()


<class 'pandas.core.frame.DataFrame'>
Index: 148517 entries, 0 to 149999
Data columns (total 14 columns):
 #   Column            Non-Null Count   Dtype         
---  ------            --------------   -----         
 0   ID                148517 non-null  int64         
 1   name              148517 non-null  object        
 2   category          148517 non-null  object        
 3   main_category     148517 non-null  object        
 4   currency          148517 non-null  object        
 5   deadline          148517 non-null  datetime64[ns]
 6   goal              148517 non-null  float64       
 7   launched          148517 non-null  datetime64[ns]
 8   pledged           148517 non-null  float64       
 9   state             148517 non-null  object        
 10  backers           148517 non-null  float64       
 11  country           148517 non-null  object        
 12  usd pledged       148517 non-null  float64       
 13  usd_pledged_real  148517 non-null  float64       
dtypes: dateti

### Importer les données

In [40]:
# Convertir le DataFrame en liste de dictionnaires (un dictionnaire par projet)
a = df_ks.to_dict(orient='records')
collection.drop()
collection.insert_many(a)


InsertManyResult([ObjectId('674f1dd6624687b74fc26ae9'), ObjectId('674f1dd6624687b74fc26aea'), ObjectId('674f1dd6624687b74fc26aeb'), ObjectId('674f1dd6624687b74fc26aec'), ObjectId('674f1dd6624687b74fc26aed'), ObjectId('674f1dd6624687b74fc26aee'), ObjectId('674f1dd6624687b74fc26aef'), ObjectId('674f1dd6624687b74fc26af0'), ObjectId('674f1dd6624687b74fc26af1'), ObjectId('674f1dd6624687b74fc26af2'), ObjectId('674f1dd6624687b74fc26af3'), ObjectId('674f1dd6624687b74fc26af4'), ObjectId('674f1dd6624687b74fc26af5'), ObjectId('674f1dd6624687b74fc26af6'), ObjectId('674f1dd6624687b74fc26af7'), ObjectId('674f1dd6624687b74fc26af8'), ObjectId('674f1dd6624687b74fc26af9'), ObjectId('674f1dd6624687b74fc26afa'), ObjectId('674f1dd6624687b74fc26afb'), ObjectId('674f1dd6624687b74fc26afc'), ObjectId('674f1dd6624687b74fc26afd'), ObjectId('674f1dd6624687b74fc26afe'), ObjectId('674f1dd6624687b74fc26aff'), ObjectId('674f1dd6624687b74fc26b00'), ObjectId('674f1dd6624687b74fc26b01'), ObjectId('674f1dd6624687b74fc26b

## Question 1  

In [41]:
#- 1) Récupérer les 5 projets ayant reçu le plus de promesse de dons.


cur = collection.find().sort("pledged", -1).limit(5)

for project in cur:
    print(project["name"], project["pledged"])
    


COOLEST COOLER: 21st Century Cooler that's Actually Cooler 13285226.36
Pebble 2, Time 2 + All-New Pebble Core 12779843.49
Expect the Unexpected. digiFilmï¿½ Camera by YASHICA 10035296.0
OUYA: A New Kind of Video Game Console 8596474.58
The Everyday Backpack, Tote, and Sling 6565782.5


In [54]:
df_ks.head(5)

ID                                               name  \
0   872782264    Scott Cooper's Solo CD "A Leg Trick" (Canceled)   
1  1326492673                                    Ohceola jewelry   
2  1688410639  Sluff Off & Harald: Two latest EGGs are Classi...   
3   156812982  SketchPlanner: Create and Plan- all in one bea...   
4  1835968190    Proven sales with custom motorcycle accessories   

         category main_category currency   deadline     goal  \
0            Rock         Music      USD 2011-09-16   2000.0   
1         Fashion       Fashion      USD 2012-08-22  18000.0   
2  Tabletop Games         Games      USD 2016-07-19   2000.0   
3       Art Books    Publishing      USD 2017-09-27  13000.0   
4       Sculpture           Art      CAD 2016-02-24   5000.0   

             launched  pledged       state  backers country  usd pledged  \
0 2011-08-17 06:31:31   1145.0    canceled     24.0      US  1145.000000   
1 2012-07-23 20:46:48   1851.0      failed     28.0      US  1851.000000   
2 2016-07-01 21:55:54   7534.0  successful    254.0      US  3796.000000   
3 2017-08-28 15:47:02  16298.0  successful    367.0      US  2670.000000   
4 2016-01-25 17:37:10      1.0      failed      1.0      CA     0.708148   

   usd_pledged_real  
0       1145.000000  
1       1851.000000  
2       7534.000000  
3      16298.000000  
4          0.738225

## Question 2

In [ ]:
#- 2) Compter le nombre de projets ayant atteint leur but.
pipeline = [
    {
        "$match": {
            "state": "successful"  
        }
    },
    {
        "$count": "nombre_de_projets" 
    }
]

cur = collection.aggregate(pipeline)
print(cur.next())

{'nombre_de_projets': 52998}


## Question 3

In [51]:
#- 3) Compter le nombre de projets pour chaque catégorie.
pipeline = [
    {
        "$group": {
            "_id": "$category",  # Regroupe par la catégorie (remplacez par le champ exact)
            "count": {"$sum": 1}  # Compte le nombre de projets par catégorie
        }
    },
    {
        "$sort": {"count": -1}  # Trie les résultats par nombre de projets, du plus grand au plus petit
    }
]

cur = collection.aggregate(pipeline)

for category in cur:
    print(category)



{'_id': 'Product Design', 'count': 8885}
{'_id': 'Documentary', 'count': 6497}
{'_id': 'Tabletop Games', 'count': 5579}
{'_id': 'Music', 'count': 5293}
{'_id': 'Shorts', 'count': 4857}
{'_id': 'Video Games', 'count': 4798}
{'_id': 'Food', 'count': 4612}
{'_id': 'Fiction', 'count': 3703}
{'_id': 'Film & Video', 'count': 3657}
{'_id': 'Nonfiction', 'count': 3390}
{'_id': 'Fashion', 'count': 3379}
{'_id': 'Art', 'count': 3358}
{'_id': 'Apparel', 'count': 2827}
{'_id': 'Theater', 'count': 2786}
{'_id': 'Rock', 'count': 2707}
{'_id': 'Technology', 'count': 2689}
{'_id': "Children's Books", 'count': 2686}
{'_id': 'Apps', 'count': 2535}
{'_id': 'Webseries', 'count': 2316}
{'_id': 'Photography', 'count': 2239}
{'_id': 'Indie Rock', 'count': 2192}
{'_id': 'Publishing', 'count': 2147}
{'_id': 'Narrative Film', 'count': 2098}
{'_id': 'Web', 'count': 2017}
{'_id': 'Comics', 'count': 1931}
{'_id': 'Crafts', 'count': 1834}
{'_id': 'Country & Folk', 'count': 1790}
{'_id': 'Design', 'count': 1641}
{'_

## Question 4

In [74]:
#- 4) Compter le nombre de projets français ayant été instanciés avant 2016.
import datetime
pipeline = [
    {
        "$match": {
            "country": "FR"            ,
            "launched": {"$lt": datetime.datetime(2016, 1, 1)}  
        }
    },
    {
        "$count": "nombre_de_projets" 
    }
]

cur = collection.aggregate(pipeline)

for category in cur:
    print(category)



{'nombre_de_projets': 330}


## Question 5

In [78]:
#- 5) Récupérer les projets américains ayant demandé plus de 200 000 dollars.

cur =collection.find({"country":"US","goal":{"$gt":200000}})

for category in cur:
    print(category)




{'_id': ObjectId('674f1dd6624687b74fc26b8a'), 'ID': 866634482, 'name': 'A CALL TO ADVENTURE', 'category': 'Film & Video', 'main_category': 'Film & Video', 'currency': 'USD', 'deadline': datetime.datetime(2012, 9, 14, 0, 0), 'goal': 287000.0, 'launched': datetime.datetime(2012, 8, 13, 23, 14, 2), 'pledged': 1465.0, 'state': 'failed', 'backers': 11.0, 'country': 'US', 'usd pledged': 1465.0, 'usd_pledged_real': 1465.0}
{'_id': ObjectId('674f1dd6624687b74fc26c3c'), 'ID': 993194166, 'name': 'Storybricks, the storytelling online RPG', 'category': 'Video Games', 'main_category': 'Games', 'currency': 'USD', 'deadline': datetime.datetime(2012, 6, 1, 0, 0), 'goal': 250000.0, 'launched': datetime.datetime(2012, 5, 1, 20, 49, 58), 'pledged': 23680.54, 'state': 'failed', 'backers': 409.0, 'country': 'US', 'usd pledged': 23680.54, 'usd_pledged_real': 23680.54}
{'_id': ObjectId('674f1dd6624687b74fc26c44'), 'ID': 1147175344, 'name': 'Shine On New World', 'category': 'Theater', 'main_category': 'Theate

## Question 6 

In [87]:
#- 6) Compter le nombre de projet ayant "Sport" dans leur nom

collection.create_index([("name", "text")])

pipeline = [
    {"$match":
        {
            "$text": { "$search": "Sport" } 
        }
    },
    {
        "$count": "nombre_de_projets" 
    }
]   

cur = collection.aggregate(pipeline)

for category in cur:
    print(category)

{'nombre_de_projets': 316}
